In [3]:
!pip install transformers datasets
import torch
from datasets import load_dataset
from transformers import BartForConditionalGeneration, BartTokenizer, Trainer, TrainingArguments
from transformers import DataCollatorForSeq2Seq

# Load dataset (replace with your actual dataset path)
dataset = load_dataset("sudeshna84/Hind-Beng-5k")

# Load BART tokenizer and model for translation
model_name = "facebook/bart-large"  # You can use a smaller variant like bart-base as well
tokenizer = BartTokenizer.from_pretrained(model_name)
model = BartForConditionalGeneration.from_pretrained(model_name)

# Preprocessing function for translation
def preprocess_function(examples):
    inputs = [f"translate Hindi to Bengali: {text}" for text in examples['hi']]  # Hindi text
    targets = examples['bn']  # Bengali text (target)
    model_inputs = tokenizer(inputs, max_length=128, truncation=True, padding="max_length")
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(targets, max_length=128, truncation=True, padding="max_length")
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

# Apply preprocessing
train_dataset = dataset["train"].map(preprocess_function, batched=True)
eval_dataset = dataset["test"].map(preprocess_function, batched=True)

# Set up data collator
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

# Set up training arguments
training_args = TrainingArguments(
    output_dir="./results",          # output directory for model checkpoints
    evaluation_strategy="epoch",     # evaluation at each epoch
    learning_rate=2e-5,              # initial learning rate
    per_device_train_batch_size=8,   # batch size per device during training
    per_device_eval_batch_size=8,    # batch size per device during evaluation
    num_train_epochs=3,              # number of training epochs
    weight_decay=0.01,               # strength of weight decay for regularization
    logging_dir="./logs",            # directory for storing logs
    logging_steps=10,                # log every 10 steps
    save_steps=500,                  # save checkpoints every 500 steps
    eval_accumulation_steps=2,       # accumulate gradients before evaluation
)

# Initialize Trainer
trainer = Trainer(
    model=model,                        # the model to train
    args=training_args,                 # training arguments
    train_dataset=train_dataset,        # training dataset
    eval_dataset=eval_dataset,          # evaluation dataset
    data_collator=data_collator,        # data collator to pad inputs
    tokenizer=tokenizer,                # tokenizer
)

# Start training
trainer.train()

# Save the fine-tuned model
model.save_pretrained("./fine_tuned_bart_model")
tokenizer.save_pretrained("./fine_tuned_bart_model")


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 484.9/484.9 kB 13.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 14.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 18.9 MB/s eta 0:00:00


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/425 [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/774k [00:00<?, ?B/s]

test-00000-of-00001.parquet:   0%|          | 0.00/336k [00:00<?, ?B/s]

...

/usr/local/lib/python3.11/dist-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
<ipython-input-3-bedd5b7803b7>:48: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.


<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: arunapriyad24 (arunapriyad24-woxsen-university) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.


/usr/local/lib/python3.11/dist-packages/transformers/modeling_utils.py:2758: UserWarning: Moving the following attributes in the config to the generation config: {'early_stopping': True, 'num_beams': 4, 'no_repeat_ngram_size': 3, 'forced_bos_token_id': 0}. You are seeing this warning because you've set generation parameters in the model config, as opposed to in the generation config.
  warnings.warn(


('./fine_tuned_bart_model/tokenizer_config.json',
 './fine_tuned_bart_model/special_tokens_map.json',
 './fine_tuned_bart_model/vocab.json',
 './fine_tuned_bart_model/merges.txt',
 './fine_tuned_bart_model/added_tokens.json')

In [8]:
from transformers import BartForConditionalGeneration, BartTokenizer

# Load the fine-tuned model and tokenizer
model = BartForConditionalGeneration.from_pretrained("./fine_tuned_bart_model")
tokenizer = BartTokenizer.from_pretrained("./fine_tuned_bart_model")

# Function to translate Hindi to Bengali using the fine-tuned model
def translate_hindi_to_bengali(hindi_text):
    # Prepare the input prompt for BART
    input_text = f"translate Hindi to Bengali: {hindi_text}"

    # Tokenize the input
    inputs = tokenizer(input_text, return_tensors="pt", max_length=128, truncation=True, padding="max_length")

    # Generate translation
    with torch.no_grad():
        outputs = model.generate(**inputs, max_length=256)


    # Decode the generated tokens to Bengali text
    translated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return translated_text

# Example sentences to translate
hindi_sentences = [
    "फिर एक बार, मन की बातें करने के लिए, आपके बीच आने का मुझे अवसर मिला है।",
    "चिल्लाकर पुकारा “अजी हो क्या!",

]

# Translate the example sentences
for hindi_sentence in hindi_sentences:
    bengali_translation = translate_hindi_to_bengali(hindi_sentence)
    print(f"Hindi: {hindi_sentence}")
    print(f"Bengali: {bengali_translation}")
    print("-" * 50)


Hindi: फिर एक बार, मन की बातें करने के लिए, आपके बीच आने का मुझे अवसर मिला है।
Bengali: একবার, মনের প্রতিবীচ কোথা লইয়া , আপনি সুরূষ এ অসব হয়।
--------------------------------------------------
Hindi: चिल्लाकर पुकारा “अजी हो क्या!
Bengali: চিল্লাকর পুকেরা “অজী হইয়া!
--------------------------------------------------


In [9]:
torch.save(model.state_dict(), 'model.pth')  # Save model weights


In [11]:
from google.colab import files
files.download('model.pth')  # Replace 'model.h5' with your model's filename


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>